In [1]:
import pandas as pd
import plotly.express as px
import numpy as np
import missingno as msn
import datetime
from pandas_profiling import ProfileReport
import sklearn

In [2]:
df = pd.read_parquet("escooter_history_2022.parquet")

In [3]:
df_3 = df.groupby(pd.Grouper(key="datetime",freq="D")).agg({"registered_customer": "count"}).reset_index()

In [10]:
df_3

datetime  registered_customer  Monat
0   2020-01-04                  985      1
1   2020-01-05                  801      1
2   2020-01-06                 1349      1
3   2020-01-07                 1562      1
4   2020-01-08                 1600      1
..         ...                  ...    ...
726 2021-12-30                 4231     12
727 2021-12-31                 8144     12
728 2022-01-01                 5932      1
729 2022-01-02                 5182      1
730 2022-01-03                 6302      1

[731 rows x 3 columns]

In [9]:
df_3["Monat"] = df_3.datetime.dt.month

In [13]:
df_3["Tag"] = pd.to_datetime(df_3["Tag"])

In [6]:
df_3.columns = ["datetime","Anzahl_pro_Stunde","Tag"]

In [5]:
df_2 = df.groupby(pd.Grouper(key="datetime",freq="M")).agg({"registered_customer": "count"}).reset_index()

In [7]:
df_2["Monat"] = df_2.datetime.dt.month

In [8]:
df_2

datetime  registered_customer  Monat
0  2020-01-31                34320      1
1  2020-02-29                53570      2
2  2020-03-31                72144      3
3  2020-04-30                94013      4
4  2020-05-31               151411      5
5  2020-06-30               162305      6
6  2020-07-31               165146      7
7  2020-08-31               152266      8
8  2020-09-30               135771      9
9  2020-10-31               144588     10
10 2020-11-30               125993     11
11 2020-12-31               108109     12
12 2021-01-31               105483      1
13 2021-02-28               113223      2
14 2021-03-31               171370      3
15 2021-04-30               200637      4
16 2021-05-31               219912      5
17 2021-06-30               234159      6
18 2021-07-31               224217      7
19 2021-08-31               237694      8
20 2021-09-30               245805      9
21 2021-10-31               240422     10
22 2021-11-30               173825     11
23 2021-12-31               171616     12
24 2022-01-31                17416      1

In [12]:
df_2.columns = ["datetime","Anzahl_pro_Tag"]

In [11]:
df_4 = pd.merge(df_3,df_2,left_on="Monat",right_on="Monat")

In [12]:
df_4

datetime_x  registered_customer_x  Monat datetime_y  \
0    2020-01-04                    985      1 2020-01-31   
1    2020-01-04                    985      1 2021-01-31   
2    2020-01-04                    985      1 2022-01-31   
3    2020-01-05                    801      1 2020-01-31   
4    2020-01-05                    801      1 2021-01-31   
...         ...                    ...    ...        ...   
1519 2021-12-29                   1424     12 2021-12-31   
1520 2021-12-30                   4231     12 2020-12-31   
1521 2021-12-30                   4231     12 2021-12-31   
1522 2021-12-31                   8144     12 2020-12-31   
1523 2021-12-31                   8144     12 2021-12-31   

      registered_customer_y  
0                     34320  
1                    105483  
2                     17416  
3                     34320  
4                    105483  
...                     ...  
1519                 171616  
1520                 108109  
1521                 171616  
1522                 108109  
1523                 171616  

[1524 rows x 5 columns]

In [13]:
px.box(df_4,x="Monat",y="registered_customer_x")

In [26]:
df_4["Anteil_pro_Tag"] = df_4.registered_customer_x / df_4.registered_customer_y

In [27]:
df_4

datetime_x  registered_customer_x        Tag datetime_y  \
0     2020-01-04 00:00:00                     16 2020-01-04 2020-01-04   
1     2020-01-04 01:00:00                     40 2020-01-04 2020-01-04   
2     2020-01-04 02:00:00                     32 2020-01-04 2020-01-04   
3     2020-01-04 03:00:00                     13 2020-01-04 2020-01-04   
4     2020-01-04 04:00:00                      1 2020-01-04 2020-01-04   
...                   ...                    ...        ...        ...   
17539 2022-01-03 19:00:00                    371 2022-01-03 2022-01-03   
17540 2022-01-03 20:00:00                    282 2022-01-03 2022-01-03   
17541 2022-01-03 21:00:00                    245 2022-01-03 2022-01-03   
17542 2022-01-03 22:00:00                    179 2022-01-03 2022-01-03   
17543 2022-01-03 23:00:00                    152 2022-01-03 2022-01-03   

       registered_customer_y  workingday  holiday  Hour  weekend  \
0                        985     0.00000      0.0     0     True   
1                        985     0.00000      0.0     1     True   
2                        985     0.00000      0.0     2     True   
3                        985     0.00000      0.0     3     True   
4                        985     0.00000      0.0     4     True   
...                      ...         ...      ...   ...      ...   
17539                   6302     0.99762      0.0    19    False   
17540                   6302     0.99762      0.0    20    False   
17541                   6302     0.99762      0.0    21    False   
17542                   6302     0.99762      0.0    22    False   
17543                   6302     0.99762      0.0    23    False   

       Anteil_pro_Tag  
0            0.016244  
1            0.040609  
2            0.032487  
3            0.013198  
4            0.001015  
...               ...  
17539        0.058870  
17540        0.044748  
17541        0.038877  
17542        0.028404  
17543        0.024119  

[17544 rows x 10 columns]

In [19]:
df_4["Hour"] = df_3.datetime.dt.hour

In [23]:
df_4["weekend"] = df_4["datetime_y"].dt.weekday > 4

In [18]:
df_4["Tag"] = df_4.datetime_x.dt.date

In [19]:
df_4.dtypes

datetime_x           datetime64[ns]
Anzahl_pro_Stunde             int64
Tag                          object
datetime_y           datetime64[ns]
Anzahl_pro_Tag                int64
Anteil_pro_Tag              float64
Hour                          int64
dtype: object

In [28]:
px.box(df_4,x="Hour",y="Anteil_pro_Tag",facet_col="weekend")

In [25]:
px.scatter(df_4,x="Hour",y="Anteil_pro_Tag",color=df_4.datetime_x.dt.quarter.astype(str),marginal_x="violin",marginal_y="box")

In [22]:
px.scatter(df_4,x="Hour",y="Anteil_pro_Tag",animation_frame="Tag",marginal_x="box",marginal_y="violin")

In [ ]:
px.box(df_4,x="Anteil_pro_Tag",y="Hour",orientation="h",notched=True)

In [ ]:
#px.violin(df_4,x="Anteil_pro_Tag",y="Hour",box=True,points="all")